In [1]:
from LMAO import AnimatePlay2
import pandas as pd
import mpl_toolkits.mplot3d.axes3d as p3
from IPython.display import HTML

In [2]:
df = pd.read_csv("/Users/Rishav/Downloads/nfl-big-data-bowl-2021/week1_norm_withz.csv")
print("hello")

/usr/local/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (12) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


hello


In [123]:
play = df[(df.gameId == 2018090905) & (df.playId == 2062)].sort_values(by = 'frameId')
import time
import numpy as np
import plotly.graph_objects as go
print(play.columns)

def animate3dplay(play):
    mapping = {'home': 'darkblue', 'away': 'fuchsia', "ball": 'brown'}
    play = play.replace({'teamAbbr': mapping})

    xx = np.linspace(0,120,120)
    yy = np.linspace(0,54,54)
    x1,y1 = np.meshgrid(xx,yy)
    field_locs = np.stack((x1,y1)).reshape(2, -1).T

    frames = []
    for i in set(play.frameId):
        small_play = play[play.frameId == i]
        t = go.Scatter3d({'type' : 'scatter3d', 
                       'x' : small_play.x, 
                       'y' : small_play.y, 
                       'z' : small_play.z, 
                       'textposition' : 'middle center',
                       "mode" : 'text+markers', 
                       'marker' : {'color' : small_play.teamAbbr}, 
                       'text' : small_play.jerseyNumber})


        frames.append(go.Frame(data = t, name = str(i)))




    d = go.Mesh3d({'type' : 'Mesh3d',
                    'x' : field_locs[:,0],
                    'y' : field_locs[:,1],
                    'z' : np.ones(field_locs.shape[0])-2,
                    'showscale' : False,
                    'colorscale' : [[0,'green'], [1, 'green']],
                    'intensity' : field_locs[:,0]
                    })


    fig = go.Figure(data = d, frames = frames)

    fig.add_trace(go.Mesh3d({'type' : 'Mesh3d',
                    'x' : field_locs[:,0],
                    'y' : field_locs[:,1],
                    'z' : np.ones(field_locs.shape[0])-2,
                    'showscale' : False,
                    'colorscale' : [[0,'green'], [1, 'green']],
                    'intensity' : field_locs[:,0]
                    }))
    
    xx = np.linspace(110,120,120)
    yy = np.linspace(0,54,54)
    x1,y1 = np.meshgrid(xx,yy)
    endzone1 = np.stack((x1,y1)).reshape(2, -1).T
    
    fig.add_trace(go.Mesh3d({'type' : 'Mesh3d',
                    'x' : endzone1[:,0],
                    'y' : endzone1[:,1],
                    'z' : np.ones(endzone1.shape[0])-1.9,
                    'showscale' : False,
                    'colorscale' : [[0,'red'], [1, 'red']],
                    'intensity' : field_locs[:,0]
                    }))
    
    xx = np.linspace(0,10,120)
    yy = np.linspace(0,54,54)
    x1,y1 = np.meshgrid(xx,yy)
    endzone2 = np.stack((x1,y1)).reshape(2, -1).T
    
    fig.add_trace(go.Mesh3d({'type' : 'Mesh3d',
                    'x' : endzone2[:,0],
                    'y' : endzone2[:,1],
                    'z' : np.ones(endzone2.shape[0])-1.9,
                    'showscale' : False,
                    'colorscale' : [[0,'pink'], [1, 'pink']],
                    'intensity' : field_locs[:,0]
                    }))


    # fig.add_trace({'type' : 'scatter3d', 
    #                    'x' : small_play.x, 
    #                    'y' : small_play.y, 
    #                    'z' : small_play.z, 
    #                    'textposition' : 'middle center',
    #                    "mode" : 'text+markers', 
    #                    'marker' : {'color' : small_play.teamAbbr}, 
    #                    'text' : small_play.jerseyNumber})

    def frame_args(duration):
        return {
                "frame": {"duration": duration},
                "mode": "immediate",
                "fromcurrent": True,
                "transition": {"duration": duration, "easing": "linear"},
            }

    sliders = [
                {
                    "pad": {"b": 10, "t": 60},
                    "len": 0.9,
                    "x": 0.1,
                    "y": 0,
                    "steps": [
                        {
                            "args": [[f.name], frame_args(0)],
                            "label": str(k),
                            "method": "animate",
                        }
                        for k, f in enumerate(fig.frames)
                    ],
                }
            ]

    # Layout
    fig.update_layout(
             title='Slices in volumetric data',
             width=1000,
             height=650,
             scene = dict(
                  aspectratio = dict(x=2, y=1, z=0.5),
                        xaxis = dict(range=[0,120],),
                         yaxis = dict(range=[0,53.3],),
                         zaxis = dict(range=[-2,12],),),
             updatemenus = [
                {
                    "buttons": [
                        {
                            "args": [None, frame_args(50)],
                            "label": "&#9654;", # play symbol
                            "method": "animate",
                        },
                        {
                            "args": [[None], frame_args(0)],
                            "label": "&#9724;", # pause symbol
                            "method": "animate",
                        },
                    ],
                    "direction": "left",
                    "pad": {"r": 10, "t": 70},
                    "type": "buttons",
                    "x": 0.1,
                    "y": 0,
                }
             ],
             sliders=sliders
    )
    return fig

fig = animate3dplay(play)
fig.show()




Index(['gameId', 'playId', 'frameId', 'event', 'nflId', 'displayName',
       'jerseyNumber', 'position', 'position_general', 'team', 'team_pos',
       'teamAbbr', 'route', 'time', 'los', 'x', 'y', 'dis', 'o', 's', 's_dir',
       's_dir_rad', 'v_x', 'v_y', 'v_theta', 'v_mag', 'a_old', 'a_x', 'a_y',
       'a_theta', 'a_mag', 'seconds_since_throw', 'z', 'z1', 'z2'],
      dtype='object')
